# Quantum information and quantum computing - Problem set 07

### _Problem 1_ : Shor's algorithm for factoring 15

In this notebook we are going to see how to implement a simple circuit of 6 qubits to factorize $N = 15$ using Python and the Qiskit quantum library provided by IBM

In [ ]:
# First, import all the useful methods

import numpy as np
import matplotlib.pyplot as plt   
import math

from qiskit_aer import QasmSimulator
from qiskit import QuantumCircuit, ClassicalRegister, QuantumRegister

In [ ]:
from qiskit_ibm_runtime import QiskitRuntimeService

# Save your credentials on disk.
# QiskitRuntimeService.save_account(channel='ibm_quantum', token=<IBM Quantum API key>)

service = QiskitRuntimeService(
    channel='ibm_quantum',
    instance='ibm-q/open/main',
)

We will surely need the circuit for $\text{QFT}^\dagger$, so we will create a function to do it

In [ ]:
def qft_dagger(circ, n):
    # TO DO: a function that takes a circuit as input
    # and appends the inverse QFT to it
    
    # Don't forget the Swaps!

Suppose now we have already made the first three steps in the Shor's algorithm and we obtained the random number $y=4$. We have that

\begin{equation*}
\text{gcd}(y,15) = 1
\end{equation*}

so we can proceed with the order-finding algorithm.

#### Build the circuit
First, we have to build the circuit. For this, we will assume that the possibile period for $y=4$ is a $2$-qubit number. This assumption is justified since we expect a small number.

Therefore, together with the $4$ qubits useful to represent the number from $0$ to $15$, we need a $6$-qubits circuit.

In [ ]:
## The initial circuit is given

# Construct the different register

first_register   = QuantumRegister(2,name="a")
second_register  = QuantumRegister(4,name="s")
classic_register = ClassicalRegister(2, name="c")

# Put together the circuit
shor_circ = QuantumCircuit(first_register,second_register,classic_register)


# In the first register , create the superposition of all the possible states

shor_circ.h(first_register[0])
shor_circ.h(first_register[1])

# And prepare the state |1>_L in the second register

shor_circ.x(second_register[0])

print(shor_circ)

# Or, with pylatexenc installed
#shor_circ.draw("mpl")

Now we need the circuit for modular exponentiation. Usually this step is the bottleneck for Shor's algorithm, since we have to apply the c-$U^{2^n}$ gates. In this case, we will contruct directly a unitary that performs

\begin{equation*}
U | z \rangle_{2}|1\rangle_{4} = | z \rangle_{2} |4^z(\text{mod}15)\rangle_{4}
\end{equation*}


This can be constructed simply by looking at the possible outcome of this operation

| z | 4^z(mod15) |
|---|------------|
| 0 | 1          |
| 1 | 4          |
| 2 | 1          |
| 3 | 4          |

In [ ]:
# TO DO: create a circuit to perform U|z>|1> as indicated above 

print(shor_circ)

- **Bonus question**: what if $y=11$?

Then we can apply the $\text{QFT}^\dagger$

In [ ]:
qft_dagger(shor_circ,2)

and measure the first two qubits

In [ ]:
## Add measurements of the first register at the end
shor_circ.measure(first_register[0],classic_register[0])
shor_circ.measure(first_register[1],classic_register[1]) 

The whole circuit looks like:

In [ ]:
## Print the final circuit

#print(shor_circ)

#### Run the circuit

In [ ]:
backend = QasmSimulator()
shots = 2048 # it is interesting seeing a single shot, since statistically we will get all the answers
results = backend.run(shor_circ, backend=backend, shots=shots).result()
answer = results.get_counts()

#### Print the results

In [ ]:
plt.suptitle("Results of order finding algorithm")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)

#### Continue the algorithm

Answer the following questions:
- What are the results of our circuit?
- What we have to do next? Do we need the continuous fraction algorithm?
- What is the final answer that we get?

### _Extra_ : using a NoiseModel of a real quantum device

We can also make our simulation more similar to the real use case by importing noise models from IBM quantum devices. This is done by importing the NoiseModel function from Qiskit

In [ ]:
##Noise Model
from qiskit_aer.noise import NoiseModel
from qiskit.providers.fake_provider import GenericBackendV2
fake_backend = GenericBackendV2(num_qubits=6)

noise_model = NoiseModel.from_backend(fake_backend)

In [ ]:
shots = 2048
results = fake_backend.run(shor_circ, backend=fake_backend, shots=shots,noise_model = noise_model).result()
answer = results.get_counts()

In [ ]:
plt.suptitle("Results of order finding algorithm")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)

Here you can see how adding the noise model showed some contribution to results different from the previous ones, generated by noise (as an example, readout error that can shift bits).